
# Algorithms.md

-------

-------

# Describe Approach

## Algorithm

**Description:** 

We first construct a similarity graph using the input graph.  Then we compute the Laplacian and its eigenvectors to do cluster based on the component associated with each node for the second eigenvector.

**Input:** 
  1. graphml object
  2. dictionary mapping indices to region labels

**Output:** dictionary mapping from region to closest region

### Pseudocode

**function** connectivity (graph, region_dict)
  1. Construct similarity graph from adjacency matrix of the graph.
  2. Compute the normalized Laplacian by doing: $L = D^{-1/2}(D - A)D^{-1/2}$, where L is the normalized laplacian, D is the Degree matrix (a diagonal matrix that measures the degree at each node), and A is the aforementioned adjacency matrix.
  3. Obtain the eigenvector associated with the second smallest eigenvalue, known as the Fiedler Vector, by taking the second column in the Laplacian constructed in step 2.
  4. The Fiedler vector should have dimensions nx1, where n is the number of nodes.  Now cluster the n components of the Fiedler vector by region label.
  5. Calculate the average for each region, and iterate through the regions to find out which region's average is closest to another's
  7. Return a dictionary, mapping from a region to its closest region.
  
**endfunction**
  
-------

-------


## Simulation


#### Easy
- Data will be contructed from 3 gaussian clusters, such that these mean of these clusters are far apart enough s.t. the clusters look distinct but close enough s.t. the graph is mostly connected.
- data points all lie on a line

We expect the connectivity algorithm to do well in this scenario because the data is essentially 1 dimensional.

#### Hard
- Data will be contructed from 3 gaussian clusters, such that these mean of these clusters are far apart enough s.t. the clusters look distinct but close enough s.t. the graph is mostly connected.

We expect the connectivity algorithm to do more poorly because there are more dimensions to consider.  Also there are only 10 points so outliers will have more impact.

# Real Data

## Fear199

In [14]:
fear = nx.read_graphml("Fear199.graphml")

# Doing the spectral embedding
fear_se = spec_clust(fear, 3)
print fear_se.shape

/usr/local/lib/python2.7/dist-packages/sklearn/manifold/spectral_embedding_.py:229: UserWarning:

Graph is not fully connected, spectral embedding may not work as expected.



(9904, 3)


In [15]:
print(fear.edges())

[('s2040', 's1703'), ('s2040', 's2042'), ('s2040', 's1859'), ('s2040', 's1918'), ('s2040', 's1944'), ('s2040', 's1945'), ('s2040', 's2259'), ('s2041', 's1765'), ('s2041', 's1767'), ('s2041', 's2218'), ('s2041', 's1738'), ('s2041', 's1647'), ('s2041', 's2452'), ('s2041', 's2217'), ('s2041', 's1842'), ('s2041', 's2457'), ('s2041', 's1769'), ('s2041', 's1977'), ('s2041', 's2096'), ('s2041', 's2160'), ('s2041', 's2190'), ('s2041', 's2191'), ('s2041', 's1947'), ('s2041', 's1602'), ('s2041', 's2392'), ('s2041', 's2454'), ('s2042', 's1764'), ('s2042', 's2219'), ('s2042', 's1703'), ('s2042', 's1918'), ('s2042', 's1944'), ('s2042', 's1945'), ('s2042', 's1772'), ('s2042', 's1948'), ('s2042', 's2320'), ('s2042', 's1894'), ('s2042', 's1770'), ('s2042', 's1880'), ('s2042', 's2537'), ('s2043', 's1766'), ('s2043', 's1980'), ('s2043', 's1646'), ('s2043', 's2451'), ('s2043', 's2455'), ('s2043', 's2287'), ('s2043', 's1943'), ('s2043', 's2583'), ('s2043', 's2128'), ('s2043', 's2130'), ('s2044', 's1984'),

In [16]:
fear_am = nx.adj_matrix(fear).todense()
print(fear_am)

[[ 0.  0.  1. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 1.  0.  0. ...,  0.  0.  0.]
 ..., 
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]


In [17]:
print(fear_se)

[[ 0.01412301 -0.01300572  0.05877919]
 [ 0.03833388 -0.03530124 -0.05413528]
 [ 0.02824602 -0.02601144  0.11841538]
 ..., 
 [ 0.02622845 -0.02415348 -0.00292075]
 [ 0.03631631 -0.03344328  0.00768157]
 [ 0.01614058 -0.01486368  0.01054801]]


In [18]:
print(fear_se[[0, 1, 2]])

[[ 0.01412301 -0.01300572  0.05877919]
 [ 0.03833388 -0.03530124 -0.05413528]
 [ 0.02824602 -0.02601144  0.11841538]]


In [19]:
fnodes = fear.nodes()
fnodes = np.array(fnodes)
print(fnodes)

['s2040' 's2041' 's2042' ..., 's9044' 's9047' 's9046']


In [20]:
print(fnodes[[0, 1, 2]])

['s2040' 's2041' 's2042']


### Plot of the graph

In [143]:
plot_graphml3d2(fear)

In [22]:
se_regions, norm_dict, se_regions_nodes = get_dict_real(fear, fear_se, 'Fear199_regions.csv')

In [62]:
c, o_c, con_graph = get_connectivity_hard(se_regions, norm_dict)
# c is a dictionary mapping from the region number to the closest region number
# print('Predicted Connectivity')
# print(c)
# print('Actual Connectivity:')
# print(o_c)

num_correct = 0
num_total = len(c)
for key in c:
    if c[key][0] == o_c[key][0]:
        num_correct += 1
print('num_correct: %d' % num_correct)
print('total: %d' % num_total)
accuracy = float(num_correct) / num_total
print('ACCURACY: %f' % accuracy)

num_correct: 27
total: 578
ACCURACY: 0.046713


In [65]:
con_adj_mat = nx.adj_matrix(con_graph).todense()
print(con_adj_mat)

[[   0.          131.00000014  342.00000003 ...,  302.00000006
   533.00000004  418.00000003]
 [ 131.00000014    0.          473.         ...,  433.          402.          287.        ]
 [ 342.00000003  473.            0.         ...,   40.00000003  875.          760.        ]
 ..., 
 [ 302.00000006  433.           40.00000003 ...,    0.          835.          720.        ]
 [ 533.00000004  402.          875.         ...,  835.            0.
   115.00000001]
 [ 418.00000003  287.          760.         ...,  720.          115.00000001
     0.        ]]


In [ ]:
coords = nx.get_node_attributes(fear,'attr')

# flip the dictionary so it maps from coordinate -> node name
coords = {v: k for k, v in coords.iteritems()}

In [60]:
print se_regions

{0.0: array([[  2.70173678e-03,   8.44510557e-04,   2.71013555e-03],
       [  2.02630258e-03,   6.33382918e-04,   2.03260166e-03],
       [  3.37717097e-03,   1.05563820e-03,   3.38766944e-03],
       [  4.05260517e-03,   1.26676584e-03,   4.06520333e-03],
       [  1.01315129e-02,   3.16691459e-03,   1.01630083e-02],
       [  1.35086839e-03,   4.22255279e-04,   1.35506778e-03],
       [  5.40347355e-03,   1.68902111e-03,   5.42027110e-03],
       [  6.75434194e-03,   2.11127639e-03,   6.77533888e-03],
       [  1.35086839e-02,   4.22255279e-03,   1.35506778e-02],
       [  1.01315129e-02,   3.16691459e-03,   1.01630083e-02],
       [  7.42977614e-03,   2.32240403e-03,   7.45287276e-03],
       [  4.72803936e-03,   1.47789348e-03,   4.74273721e-03],
       [  1.35086839e-03,   4.22255279e-04,   1.35506778e-03],
       [  3.37717097e-03,   1.05563820e-03,   3.38766944e-03],
       [ -5.81612075e-02,   5.20020349e-02,   1.11919496e-02],
       [  4.05260517e-03,   1.26676584e-03,   4.0

In [59]:
for region_name, val in c.iteritems():
#     print region_name
    closest_region = val[0]
    connectivity = val[1]
    se_points = se_regions[region_name]


0.0
[10720.0, 0.010926097463584356]
2.0
[148.0, 8.2931303834563296e-16]
7.0
[657.0, 1.1663255089316315e-05]
8.0
[1046.0, 1.2594223431356763e-05]
9.0
[816.0, 2.5870638198195315e-15]
10.0
[122.0, 1.1492239613198318e-05]
12.0
[197.0, 6.2286538194056395e-16]
15.0
[537.0, 1.0204392888504386e-15]
17.0
[82.0, 1.2890966149548291e-05]
19.0
[186.0, 9.9121735485990939e-16]
20.0
[41.0, 8.4171817626155369e-16]
23.0
[10710.0, 2.0272980813358207e-15]
26.0
[1096.0, 5.3245294970687352e-06]
27.0
[929.0, 3.1381503685084587e-15]
28.0
[564.0, 3.1250826987448402e-06]
33.0
[68.0, 2.2608771402621282e-05]
36.0
[1105.0, 1.2563393454150076e-15]
41.0
[774.0, 2.5935430391699172e-16]
42.0
[796.0, 2.2565287042931063e-16]
45.0
[898.0, 3.6763817658453959e-15]
50.0
[975.0, 1.5169936731915198e-15]
52.0
[842.0, 1.0687782842580744e-05]
53.0
[1081.0, 8.8531438818040462e-15]
55.0
[1104.0, 4.4190697346502742e-16]
56.0
[1020.0, 2.2354572249970669e-05]
59.0
[1085.0, 2.4492835683447225e-05]
60.0
[678.0, 6.8247866578629301e-16]


In [ ]:
fear.add_edge(e1, e2, weight=connectivity)

### Plot of the Eigenvector embedding

In [111]:
plot_connectivity3d(se_regions, detail=False)

## Analysis

* We output connectivity results as a dictionary, mapping from region to the closest region
* For a given region A, we defined a closest region prediction P as being 'correct' if for region A in the actual brain, the closest region by distance is P
* we defined distance between 2 regions as finding the centroids of the 2 regions and then taking the Euclidian distance between the centroids.
* Using Euclidian distance as a metric for ground truth, we found that:
    * num correct predictions (matchings): 10
    * total number of regions: 578
    * ACCURACY: 0.017301
    

In [133]:
analyze_real(fear, fear_se, 'Fear199_regions.csv')

Predicted Connectivity
OrderedDict([(0.0, [982.0, 0.00013804333042255419]), (2.0, [267.0, 0.00013598484137252814]), (7.0, [133.0, 0.00013759163582362059]), (8.0, [821.0, 0.0010805638329164555]), (9.0, [310.0, 0.00013345669507677782]), (10.0, [187.0, 7.4334092768035749e-05]), (12.0, [1105.0, 0.0014504688807444848]), (15.0, [1102.0, 0.00085551384168909366]), (17.0, [797.0, 7.0202000813253154e-05]), (19.0, [10692.0, 8.082529859385415e-05]), (20.0, [718.0, 0.00026746147399495232]), (23.0, [422.0, 0.00025726644711446814]), (26.0, [391.0, 0.00015644433568203335]), (27.0, [661.0, 0.00015218296953466935]), (28.0, [733.0, 6.8033702797304352e-05]), (33.0, [243.0, 0.00018144997325240521]), (36.0, [427.0, 0.00017274225505062144]), (41.0, [92.0, 0.00012121138077119226]), (42.0, [562.0, 0.0039874332528289586]), (45.0, [115.0, 0.00011627475578657696]), (50.0, [780.0, 0.00015672378825645761]), (52.0, [251.0, 4.7923810461066336e-05]), (53.0, [377.0, 0.0033684238026254758]), (55.0, [1096.0, 0.0005607965

# Code

## Imports and plotting functions

In [1]:
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
from plotly.graph_objs import *
from plotly import tools
import plotly

import os

import csv,gc  # garbage memory collection :)

import numpy as np
from numpy import linalg as LA

import csv
import re
import matplotlib
import time
import seaborn as sns

from collections import OrderedDict

import ast

import networkx as nx
import math
from sklearn.manifold import spectral_embedding as se

import scipy.sparse as sp

plotly.offline.init_notebook_mode()

In [2]:
def plot_connectivity3d(dictionary, orig_dict=None, detail=True):
    current_palette = sns.color_palette("husl", len(dictionary.keys()))
    Xe = []
    Ye = []
    Ze = []
    data = []
    avg_dict = OrderedDict()
    orig_avg_dict = OrderedDict()
    con_dict = OrderedDict()
    orig_con_dict = OrderedDict()
    i = 0
    
    if orig_dict != None:
        # Getting the original averages.
        for key, region in orig_avg_dict.iteritems():
            tmp_x = []
            tmp_y = []

            for coord in region:    
                tmp_x.append(coord[0])
                tmp_y.append(coord[1])
            orig_avg_dict[key] = [np.mean(tmp_x), np.mean(tmp_y)]
    
        # Getting connectivity for original points.
        for key, avg in orig_avg_dict.iteritems():
            min_key = ''
            min_diff = float('inf')
            for key2, avg2 in orig_avg_dict.iteritems():
                if key2 == key:
                    continue
                avg_np = np.array(avg)
                avg2_np = np.array(avg2)
                diff = np.linalg.norm(avg_np - avg2_np)
                if diff < min_diff:
                    min_diff = diff
                    min_key = key2

            orig_con_dict[key] = [min_key, min_diff]
            
            
    for key, region in dictionary.iteritems():
        X = []
        Y = []
        Z = []
        tmp_x = []
        tmp_y = []
        tmp_z = []
        region_col = current_palette[i]
        region_col_lit = 'rgb' + str(region_col)
        i += 1
        for coord in region:    
            X.append(coord[0])
            Y.append(coord[1])
            Z.append(coord[2])
            tmp_x.append(coord[0])
            tmp_y.append(coord[1])
            tmp_z.append(coord[2])
        avg_dict[key] = [[np.mean(tmp_x), np.mean(tmp_y), np.mean(tmp_z)]]
            
        trace_scatter = Scatter3d(
                x = X, 
                y = Y,
                z = Z,
                name=key,
                mode='markers',
                marker=dict(
                    size=10,
                    color=region_col_lit, #'purple',                # set color to an array/list of desired values
                    colorscale='Viridis',   # choose a colorscale
                    opacity=0.5
                )
        )
        avg_scatter = Scatter3d(
                x = [avg_dict[key][0][0]],
                y = [avg_dict[key][0][1]],
                z = [avg_dict[key][0][2]],
                mode='markers',
                name=key+'_avg',
                marker=dict(
                    size=10,
                    color=region_col_lit,
                    colorscale='Viridis',
                    line=dict(
                        width = 2,
                        color = 'rgb(0, 0, 0)'
                    )
                )
        )
        data.append(trace_scatter)
        data.append(avg_scatter)
        
#     print('plot avgdict')
#     print(avg_dict)
        
    locations = avg_dict.keys()
#     print locations
    for i, key in enumerate(avg_dict):
#         if i + 1 == len(locations):
#             continue
#         print 'start' + str(i)
        tmp = []
        for j in range(len(locations)):
            if j == i:
                continue
            p1 = np.asarray(avg_dict[key][0])
            p2 = np.asarray(avg_dict[locations[j]][0])
            dist = LA.norm(p1 - p2)
#             dist = (math.pow(avg_dict[key][0][0]-avg_dict[locations[j]][0][0],2) + 
#                        math.pow(avg_dict[key][0][1]-avg_dict[locations[j]][0][1],2) +
#                        math.pow(avg_dict[key][0][2]-avg_dict[locations[j]][0][2],2))
            tmp.append(dist)
#             print dist
        newmin = tmp.index(min(tmp))
        if newmin >= i:
            newmin += 1
#         print newmin
        if detail:
            print "region " + key + ": " + locations[newmin]
        tmp2 = avg_dict.keys()[newmin]
        Xe+=[avg_dict[key][0][0],avg_dict[tmp2][0][0],None]
        Ye+=[avg_dict[key][0][1],avg_dict[tmp2][0][1],None]
        Ze+=[avg_dict[key][0][2],avg_dict[tmp2][0][2],None]
#     print Xe
#     print Ye
    
    trace_edge = Scatter3d(x=Xe,
                y=Ye,
                z=Ze,
                mode='lines',
                line=Line(color='rgb(0,0,0)', width=3),
                hoverinfo='none'
    )

    data.append(trace_edge)
    
    for key, avg in avg_dict.iteritems():
        min_key = ''
        min_diff = float('inf')
        for key2, avg2 in avg_dict.iteritems():
            if key2 == key:
                continue
            avg_np = np.array(avg)
            avg2_np = np.array(avg2)
            diff = np.linalg.norm(avg_np - avg2_np)
            if diff < min_diff:
                min_diff = diff
                min_key = key2
        
        con_dict[key] = [min_key, min_diff]
    
    # Printing results
    if detail:
        print('connectivity dict:')
        print(con_dict)

        if orig_dict != None:
            print('orig con dict:')
            print(orig_con_dict)
    
    layout = Layout(
#         margin=dict(
#             l=0,
#             r=0,
#             b=0,
#             t=0
#         ),
        paper_bgcolor='rgb(255,255,255)',
        plot_bgcolor='rgb(255,255,255)'
    )
        
    fig = Figure(data=data, layout=layout)
    iplot(fig, validate=False)

In [3]:
import pandas as pd

def plot_graphml3d2(G):
    g = G

    # grab the node positions from the graphML file
    V = nx.number_of_nodes(g)
    attributes = nx.get_node_attributes(g, 'attr')
    node_positions_3d = pd.DataFrame(columns=['x', 'y', 'z'], index=range(V))
    for n in g.nodes_iter():
        node_positions_3d.loc[n] = [int((re.findall('\d+', str(attributes[n])))[0]),
                                    int((re.findall('\d+', str(attributes[n])))[1]),
                                    int((re.findall('\d+', str(attributes[n])))[2])]

    # grab edge endpoints
    edge_x = []
    edge_y = []
    edge_z = []

    for e in g.edges_iter():
        # strippedSource = int(e[0].replace('s', ''))
        # strippedTarget = int(e[1].replace('s', ''))
        source_pos = node_positions_3d.loc[e[0]]
        target_pos = node_positions_3d.loc[e[1]]

        edge_x += [source_pos['x'], target_pos['x'], None]
        edge_y += [source_pos['y'], target_pos['y'], None]
        edge_z += [source_pos['z'], target_pos['z'], None]


    # node style
    node_trace = Scatter3d(x=[x for x in node_positions_3d['x']],
                           y=[x for x in node_positions_3d['y']],
                           z=[x for x in node_positions_3d['z']],
                           mode='markers',
                           # name='regions',
                           marker=Marker(symbol='dot',
                                         size=6,
                                         opacity=0.5,
                                         color='purple'),
                           # text=[str(r) for r in range(V)],
                           # text=atlas_data['nodes'],
                           hoverinfo='text')

    # edge style
    edge_trace = Scatter3d(x=edge_x,
                           y=edge_y,
                           z=edge_z,
                           mode='lines',
                           line=Line(color='cyan', width=1),
                           hoverinfo='none')

    # axis style
    axis = dict(showbackground=False,
                showline=False,
                zeroline=False,
                showgrid=False,
                showticklabels=False)

    plot_title = 'graphml plot'
    # overall layout
    layout = Layout(title=plot_title,
                    width=800,
                    height=900,
                    showlegend=False,
                    scene=Scene(xaxis=XAxis(axis),
                                yaxis=YAxis(axis),
                                zaxis=ZAxis(axis)),
                    margin=Margin(t=50),
                    hovermode='closest',
                    paper_bgcolor='rgba(0,0,0,0)',
                    plot_bgcolor='rgb(255,255,255)')

    data = Data([node_trace, edge_trace])
    fig = Figure(data=data, layout=layout)
    iplot(fig, validate=False)

In [4]:
def get_connectivity(eig_dict, orig_dict=None):
    eigenvector_index = 1 # the second smallest eigenvector
    avg_dict = {}
    orig_avg_dict = OrderedDict()
    
    # dict that maps from region to most connected region
    con_dict = OrderedDict()
    
    orig_con_dict = OrderedDict()
    
    if orig_dict != None:
        # Getting the original averages.
        for key, region in orig_dict.iteritems():
            tmp_x = []
            tmp_y = []

            for coord in region:
                tmp_x.append(coord[0])
                tmp_y.append(coord[1])
            orig_avg_dict[key] = [np.mean(tmp_x), np.mean(tmp_y)]
            
#         print 'orignal averages'
#         print orig_avg_dict
    
        # Getting connectivity for original points.
        for key, avg in orig_avg_dict.iteritems():
            min_key = ''
            min_diff = float('inf')
            for key2, avg2 in orig_avg_dict.iteritems():
                if key2 == key:
                    continue
                avg_np = np.array(avg)
                avg2_np = np.array(avg2)
                diff = np.linalg.norm(avg_np - avg2_np)
                if diff < min_diff:
                    min_diff = diff
                    min_key = key2

            orig_con_dict[key] = [min_key, min_diff]
            
    
    # Getting the average second eigenvector component for each of the regions
    for key, region in eig_dict.iteritems():
#         print(key)
        y_vals = []
        
        for j in range(len(region)):
            y_vals.append(region[j][eigenvector_index])
        avg = np.mean(y_vals)
        avg_dict[key] = avg
    
    for key, avg in avg_dict.iteritems():
        min_key = ''
        min_diff = float('inf')
        for key2, avg2 in avg_dict.iteritems():
            if key2 == key:
                continue
            diff = np.sqrt(np.square(avg - avg2))
            if diff < min_diff:
                min_diff = diff
                min_key = key2
        
        con_dict[key] = [min_key, min_diff]
    
    con_dict = OrderedDict(sorted(con_dict.items()))
#     con_dict = sorted(con_dict.items())
    
    if orig_dict == None:
        return con_dict
    else:
        return con_dict, orig_con_dict

In [56]:
def get_connectivity_hard(eig_dict, orig_dict=None):
    eigenvector_index = 1 # the second smallest eigenvector
    avg_dict = {}
    orig_avg_dict = OrderedDict()
    
    # dict that maps from region to most connected region
    con_dict = OrderedDict()
    
    orig_con_dict = OrderedDict()
    
    if orig_dict != None:
        # Getting the original averages.
        for key, region in orig_dict.iteritems():
            tmp_x = []
            tmp_y = []
            y_vals = []
            
            for j in range(len(region)):
                y_vals.append(region[j])
            y_vals = np.array(y_vals)
            x_avg = np.mean(y_vals[:,0])
            y_avg = np.mean(y_vals[:,1])
            z_avg = np.mean(y_vals[:,2])
            orig_avg_dict[key] = [x_avg, y_avg, z_avg]
#             avg = np.mean(y_vals)
#             orig_avg_dict[key] = avg
            
#         print 'orignal averages'
#         print orig_avg_dict
    
        # Getting connectivity for original points.
        for key, avg in orig_avg_dict.iteritems():
            min_key = ''
            min_diff = float('inf')
            for key2, avg2 in orig_avg_dict.iteritems():
                if key2 == key:
                    continue
                avg_np = np.array(avg)
                avg2_np = np.array(avg2)
                diff = np.linalg.norm(avg_np - avg2_np)
                if diff < min_diff:
                    min_diff = diff
                    min_key = key2

            orig_con_dict[float(key)] = [float(min_key), min_diff]
            
    
    # Getting the average first 2 eigenvector components for each of the regions
    for key, region in eig_dict.iteritems():
#         print(key)
        y_vals = []
        
        for j in range(len(region)):
            y_vals.append(region[j])
        y_vals = np.array(y_vals)
        x_avg = np.mean(y_vals[:,0])
        y_avg = np.mean(y_vals[:,1])
        z_avg = np.mean(y_vals[:,2])
        avg_dict[key] = [x_avg, y_avg, z_avg]
        
#     print('getcon avg_dict')
#     print(avg_dict)
    
    # Computing connectivity between regions using the distance between averages
    for key, avg in avg_dict.iteritems():
        min_key = ''
        min_diff = float('inf')
        for key2, avg2 in avg_dict.iteritems():
            if key2 == key:
                continue
            avg_np = np.array(avg)
            avg2_np = np.array(avg2)
            diff = np.linalg.norm(avg_np - avg2_np)
            if diff < min_diff:
                min_diff = diff
                min_key = key2
        
        con_dict[float(key)] = [float(min_key), min_diff]
    
    con_dict = OrderedDict(sorted(con_dict.items()))
    orig_con_dict = OrderedDict(sorted(orig_con_dict.items()))
    
    g = create_connectivity_graph(orig_avg_dict, con_dict)
    
    if orig_dict == None:
        return con_dict
    else:
        return con_dict, orig_con_dict, g

In [60]:
def create_connectivity_graph(orig_avg_dict, se_avg_dict):
    g=nx.Graph()
    for key, avg in se_avg_dict.iteritems():
        for key2, avg2 in se_avg_dict.iteritems():
            avg_np = np.array(avg)
            avg2_np = np.array(avg2)
            diff = np.linalg.norm(avg_np - avg2_np)
            g.add_edge(key, key2, weight=diff)
            
    # Setting the coordinate attribute for each region node to the average of that region.
    for key, avg in orig_avg_dict.iteritems():
        g.node[key]['attr'] = avg
    
    return g

In [48]:
a = nx.Graph()
a.add_edge(1,2,weight=5)
# a.add_node(1, asdf='asdf')
print(a.edges())

[(1, 2)]


In [52]:
# a.add_node(1, )
a.node[1]['attr'] = [1, 2, 3]

In [53]:
# a.add_node(4, attr=[1,2,3])

In [54]:
print(a.edges())
print(a.nodes(data=True))
print(a[1])

[(1, 2)]
[(1, {'attr': [1, 2, 3]}), (2, {})]
{2: {'weight': 5}}


## Function for doing the clustering

In [6]:
def spec_clust(graphx, num_components):
    adj_mat = nx.adjacency_matrix(graphx)
#     result = se(adj_mat, n_components=num_components, drop_first=True)
    result = se(adj_mat, n_components=num_components, drop_first=False)

    return result

## Functions for doing the analysis

In [7]:
def get_dict_hard(graphx, a2out):
    nodelist = graphx.nodes()
    a_arr = np.zeros(10, dtype=np.int)
    b_arr = np.zeros(10, dtype=np.int)
    c_arr = np.zeros(10, dtype=np.int)
#     d_arr = np.zeros(10, dtype=np.int)
    for ind, i in enumerate(nodelist):
#         print('i: %s' % i)
        region = int(float(i))/10
        place = int(float(i)) % 10
        if region == 0:
            a_arr[place] = int(ind)
    #         a_list.append(int(float(i)))
        elif region == 1:
            b_arr[place] = int(ind)
    #         b_list.append(int(float(i)))
        elif region == 2:
            c_arr[place] = int(ind)
    #         c_list.append(int(float(i)))
#         elif region == 3:
#             d_arr[place] = int(ind)
#     #         d_list.append(int(float(i)))

    a_region = a2out[a_arr.tolist()]  # V[0:9,:].mean(axis=0)
    print a_arr.tolist()
    b_region = a2out[b_arr.tolist()]  # V[10:19,:].mean(axis=0)
    c_region = a2out[c_arr.tolist()]  # V[20:29,:].mean(axis=0)
#     d_region = a2out[d_arr.tolist()]  # V[20:29,:].mean(axis=0)
#     se_regions = OrderedDict([('a', a_region),('b', b_region),('c', c_region),('d', d_region)])
    se_regions = OrderedDict([('a', a_region),('b', b_region),('c', c_region)])

    
    return se_regions

In [8]:
def analyze_hard(G, norm_dict, se_result):
    se_regions = get_dict_hard(G, se_result)
#     plot_connectivity(se_regions, norm_dict)
#     print('se regions')
#     print(se_regions)
    c, o_c = get_connectivity_hard(se_regions, norm_dict)
    print('Predicted Connectivity:')
    print(c)
    print('Actual Connectivity:')
    print(o_c)
    
    num_correct = 0
    num_total = len(c)
    for key in c:
        if c[key][0] == o_c[key][0]:
            num_correct += 1
            
    accuracy = float(num_correct) / num_total
    print('ACCURACY: %f' % accuracy)
        
    plot_connectivity3d(se_regions)

In [9]:
def analyze_real(graph, se_result, input_path):
    se_regions, norm_dict = get_dict_real(graph, se_result, input_path)
    c, o_c = get_connectivity_hard(se_regions, norm_dict)
    # c is a dictionary mapping from the region number to the closest region number
    print('Predicted Connectivity')
    print(c)
    print('Actual Connectivity:')
    print(o_c)

    num_correct = 0
    num_total = len(c)
    for key in c:
        if c[key][0] == o_c[key][0]:
            num_correct += 1
            
    accuracy = float(num_correct) / num_total
    print('ACCURACY: %f' % accuracy)
    
#     rplot_connectivity3d(se_regions)

# def analyze_real(G, norm_dict, se_result):
#     se_regions = get_dict_hard(G, se_result)
# #     plot_connectivity(se_regions, norm_dict)
# #     print('se regions')
# #     print(se_regions)
#     c, o_c = get_connectivity_hard(se_regions, norm_dict)
# #     print('Predicted Connectivity:')
# #     print(c)
# #     print('Actual Connectivity:')
# #     print(o_c)
    
#     num_correct = 0
#     num_total = len(c)
#     for key in c:
#         if c[key][0] == o_c[key][0]:
#             num_correct += 1
            
#     accuracy = float(num_correct) / num_total
#     print('ACCURACY: %f' % accuracy)
        
# #     plot_connectivity3d(se_regions)

In [10]:
class SparseMatrix:
    def __init__(self, x, y, z):
#         self._max_index = 0
        x_dim = x
        y_dim = y
        z_dim = z
        self._vector = {}

    def add(self, index, value):
        # vector starts at index one, because it reads from the file and the file
        # always has the index of the features start at 1
        self._vector[index] = value
#         if index > self._max_index:
#             self._max_index = index

    def get(self, index):
        # if the index doesn't exist in the dict, return 0 because it's sparse anyways
        if index in self._vector:
            return self._vector[index]
        return -1

    def get_sparse_matrix(self):
        return self._vector
        # return self._vector.keys()

#     def get_full_vector(self, size=None):
#         """ Returns a full vector of features as a numpy array. """
#         size = (self._max_index + 1) if size == None else size
#         full_vector = np.zeros(size)  # 0 indexed
#         for key, value in self._vector.iteritems():
#             full_vector[key] = value

#         return full_vector

    def __str__(self):
        return str(self._vector)

In [11]:
def add_to_dict(d, region, index):
    if region in d:
        d[region].append(index)
    else:
        d[region] = [index]
        
    return d

def get_adj_mat(regions_path):
    points = np.genfromtxt(regions_path, delimiter=',')
    x_dim = np.max(points[:,0])
    y_dim = np.max(points[:,1])
    z_dim = np.max(points[:,2])
    am = SparseMatrix(x_dim, y_dim, z_dim)
    for point in points:
        am.add(tuple(point[0:3]), point[4])
        
    return am

def get_dict_real(g, se_result, regions_path):
    nodes = g.nodes()
    points = np.genfromtxt(regions_path, delimiter=',')
    orig_dict = OrderedDict()
    d = {}
    
    sparse_mat = get_adj_mat(regions_path)

    for index, node in enumerate(nodes):        
        s = g.node[node]['attr']
        point = ast.literal_eval(s)
        region = sparse_mat.get(tuple(point))
#         if region == -1:
#             # error
#             print 'FUCK'
        add_to_dict(d, region, index)
    
    for point in points:
        region = point[4]
#         if region in orig_dict:
#             orig_dict[region] = np.vstack((orig_dict[region], point[0:3]))
#         else:
#             orig_dict[region] = np.array([point[0:3]])
        add_to_dict(orig_dict, region, point[0:3])
    
    se_regions_nodes = {}
    se_regions = {}
    for key, value in d.iteritems():
        index_list = value
        nodes_arr = np.array(nodes)
        pt_names = nodes_arr[index_list]
        se_pts = se_result[index_list]
        nodes_to_se = dict(zip(pt_names, se_pts))  # maps from node names to embedded point coordinates
        se_regions_nodes[key] = nodes_to_se  
        se_regions[key] = se_pts
    
    return se_regions, orig_dict, se_regions_nodes

# def analyze_real(graph, se_result, input_path):
#     se_regions = get_dict_real(graph, se_result, input_path)
# #     c = get_connectivity_tot(se_regions)
# #     print('Predicted Connectivity')
# #     print(c)
#     plot_connectivity3d(se_regions)

In [12]:
a = np.array([0, 1, 2, 3, 4])
b = a[[2, 4]]
print(b)

[2 4]


In [13]:
fnodes = fear.nodes()
print(fnodes)


NameError: name 'fear' is not defined

In [81]:
node = fnodes[[0, 1]]
print(node)

TypeError: list indices must be integers, not list

In [42]:
p = fear.node[node]['attr']
print(p)

[150, 213, 484]


In [45]:
coords = nx.get_node_attributes(fear,'attr')

In [46]:
print(coords)

{'s2040': u'[150, 213, 484]', 's2041': u'[150, 215, 169]', 's2042': u'[150, 215, 497]', 's2043': u'[150, 217, 340]', 's2044': u'[150, 244, 178]', 's2045': u'[150, 246, 158]', 's2046': u'[150, 263, 479]', 's2047': u'[151, 23, 321]', 's2048': u'[151, 52, 408]', 's2049': u'[151, 63, 182]', 's2734': u'[171, 54, 382]', 's2738': u'[171, 81, 383]', 's2739': u'[171, 87, 296]', 's2735': u'[171, 62, 148]', 's3271': u'[186, 171, 463]', 's2732': u'[171, 30, 277]', 's2733': u'[171, 51, 226]', 's2730': u'[171, 20, 342]', 's2731': u'[171, 28, 375]', 's6535': u'[279, 194, 425]', 's7559': u'[306, 230, 419]', 's7558': u'[306, 210, 216]', 's7009': u'[291, 253, 380]', 's7008': u'[291, 250, 169]', 's7555': u'[306, 169, 424]', 's7554': u'[306, 165, 224]', 's7005': u'[291, 244, 473]', 's7004': u'[291, 239, 125]', 's7551': u'[306, 160, 290]', 's7550': u'[306, 154, 500]', 's8806': u'[351, 189, 240]', 's8551': u'[342, 86, 247]', 's8552': u'[342, 89, 305]', 's8553': u'[342, 92, 323]', 's8802': u'[351, 177, 269]'

In [47]:
l = [1, 2, 3]
print(l)
print(str(l))

[1, 2, 3]
[1, 2, 3]


In [48]:
coords = {v: k for k, v in coords.iteritems()}

In [49]:
print(coords)

{u'[110, 57, 308]': 's1046', u'[301, 157, 231]': 's7369', u'[420, 152, 288]': 's9890', u'[306, 160, 290]': 's7551', u'[125, 84, 401]': 's1412', u'[261, 209, 383]': 's5828', u'[201, 99, 128]': 's3800', u'[164, 173, 347]': 's2482', u'[192, 261, 446]': 's3513', u'[314, 154, 250]': 's7790', u'[170, 85, 360]': 's2703', u'[117, 113, 265]': 's1223', u'[186, 241, 171]': 's3282', u'[249, 212, 333]': 's5382', u'[403, 92, 360]': 's9760', u'[303, 216, 399]': 's7463', u'[163, 276, 402]': 's2462', u'[306, 230, 419]': 's7559', u'[215, 249, 264]': 's4276', u'[124, 199, 334]': 's1400', u'[65, 217, 262]': 's183', u'[80, 138, 300]': 's412', u'[174, 161, 353]': 's2868', u'[219, 203, 63]': 's4383', u'[358, 207, 221]': 's8995', u'[315, 72, 185]': 's7808', u'[325, 261, 301]': 's8135', u'[110, 74, 178]': 's1047', u'[136, 167, 446]': 's1673', u'[199, 158, 160]': 's3738', u'[144, 160, 56]': 's1871', u'[142, 248, 225]': 's1845', u'[107, 195, 198]': 's1000', u'[312, 135, 362]': 's7738', u'[192, 83, 230]': 's3483'

In [55]:
l = [110, 57, 308]
print(coords[str(l)])

s1046
